In [1]:
%%HTML
<script>
  // Hide code cells by default.
  var HIDE_CODE_CELLS = true;

  function toggle_code_cells() {
    if (HIDE_CODE_CELLS){
      $('div.input').hide();
    } else {
      $('div.input').show();
    }
    HIDE_CODE_CELLS = !HIDE_CODE_CELLS;
  }

  $(document).ready(toggle_code_cells);
</script>

<a href="javascript:toggle_code_cells()">[Toggle Code Cells]</a>

# Validation of NanoAOD against HeppyV25
---

The 2016 MC Znn signal sample (`ZH_HToBB_ZToNuNu_M125_13TeV_powheg_pythia8`) was ntuplized using HeppyV25 for the 2016 analysis. A copy of this ntuple is stored under the following EOS directory at cmslpc:

`root://cmseos.fnal.gov///store/group/lpchbb/HeppyNtuples/V25/ZH_HToBB_ZToNuNu_M125_13TeV_powheg_pythia8/`

For the 2017 analysis, the ntuple format has been migrated to NanoAOD. To compare the two formats and validate important distributions, Stephane has ntuplized a small portion of the 2016 MC Znn signal sample using NanoAOD. These can be located using CMSDAS at the following [link][Znn_NanoAOD_Ntuples]. The NanoAOD post-processed ntuples used corresponds to the "NanoPost4" CRAB submission.

The HeppyV25 and NanoAOD ntuples have been hadded and stored on EOS at cmslpc. You may find them at:

- HeppyV25  
  root://cmseos.fnal.gov///store/user/sjwang/ZnnHbb_Ntuple_Validation/Znn_HeppyV25.root
- NanoAOD  
  root://cmseos.fnal.gov///store/user/sjwang/ZnnHbb_Ntuple_Validation/Znn_NanoPost4.root

[Znn_NanoAOD_Ntuples]: https://cmsweb.cern.ch/das/request?instance=prod%2Fphys03&input=file+dataset%3D%2FZH_HToBB_ZToNuNu_M125_13TeV_powheg_pythia8%2Fscoopers-NanoTestPost-f64d1fc6d0aff52acf7debc448857e96%2FUSER

## Event Weights
---

For the comparison, the histograms are normalized by their respective integrals in lieu of a target luminosity because I'm unsure of how to retrieve the number of positively and negatively weighted events over the entire MC sample from a NanoAOD ntuple.

All the events are weighted only by the expression "sign(genWeight)".

## Analysis Phase Space Selection
---

Further selections are applied to both ntuples on top of the baseline selection in order to validate the same distributions but in a phase space closer to that of the actual analysis. This is still a broad selection in the sense that these cuts are those shared amongst the signal and control region definitions. The selections are the following:

- **Vector Boson Selection**  
  MET > 170 GeV
- **MET Triggers**  
  The MET triggers used by the 2016 analysis. Events must pass any of the following MET triggers: HLT_PFMET110_PFMHT110_IDTight, HLT_PFMET120_PFMHT120_IDTight, HLT_BIT_HLT_PFMET170_HBHE_BeamHaloCleaned, HLT_PFMET170_NoiseCleaned, HLT_PFMET170_HBHECleaned.  
- **Higgs Boson Selection**  
  $m(\textrm{jj}) < 500 \textrm{ GeV}$ and $p_{\textrm{T}}(\textrm{jj}) > 120 \textrm{ GeV}$
- **VH Selection**  
  $\Delta\phi(V, \textrm{jj}) > 2$
- **Higgs Jet 1 Selection**  
  $p_{\textrm{T}}(\textrm{j1}) > 60 \textrm{ GeV}$ and $\textrm{CMVA}_{\textrm{max}} > -0.5884$ and Loose Jet ID and Pileup ID  
  Note that the value of -0.5884 is defined to be the loose working point for the CMVA algorithm according to [BtagPOG recommendations][BtagWorkingPoints].
- **Higgs Jet 2 Selection**  
  The same as for Higgs Jet 1, except $p_{\textrm{T}}(\textrm{j1}) > 35 \textrm{ GeV}$.  
- **QCD Mitigation**  
  No jets with $\Delta\phi(MET, j) < 0.5$ for jets with $p_{\textrm{T}} > 30 \textrm{ GeV}$ and Pileup ID.
  
[BtagWorkingPoints]: https://twiki.cern.ch/twiki/bin/viewauth/CMS/BtagRecommendation80XReReco#Supported_Algorithms_and_Operati

Recall that the baseline selection consisted of the following cuts:

- **Vector Boson Selection**  
  The Vtype is either 2 (Wmn), 3 (Wen), or 4 (Znn). In the [HeppyV25 VHbb analyzer][VHbbAnalyzer.py], events without selected leptons and MET > 80 GeV were assigned a Vtype of 4. The new [NanoAOD VHbb analyzer][VHbbProducer.py] increases this threshold to MET > 150 GeV, so a MET > 150 GeV cut is applied for a fair comparison.
- **Higgs Boson Selection**  
  Require $m(\textrm{jj}) > 0 \textrm{ GeV}$. 
- **MET Filters**  
  The MET filters recommended by the JetMET POG for 2016 analyses. Events must pass all of the following MET filters: Flag_goodVertices, Flag_GlobalTightHalo2016Filter, Flag_HBHENoiseFilter, Flag_HBHENoiseIsoFilter, Flag_EcalDeadCellTriggerPrimitiveFilter.
  
[VHbbAnalyzer.py]: https://github.com/vhbb/cmssw/blob/7121eee182cd35fc8b96aa2f24a7ac0cd48f5ad3/VHbbAnalysis/Heppy/python/VHbbAnalyzer.py#L445-L448
[VHbbProducer.py]: https://github.com/vhbb/nanoAOD-tools/blob/14bce3dca68288e65b2daefce755d65914a3765d/python/postprocessing/analysis/higgs/vhbb/VHbbProducer.py#L72-L74

In [2]:
import uuid

import ROOT
import cms_figure

%jsroot on

def histogram(self, variable, nbins, xmin, xmax, weights='', norm=True):
    """Create and return a ROOT histogram from a TTree.
    
    This method is dynamically patched onto the ROOT.TTree class.

    Parameters
    ----------
    tree : ROOT.TTree
        The TTree containing the branches used to generate the histogram.
    variable : str
        The variable for which the histogram is created. This can also be
        a valid TTreeFormula.
    nbins : int
        The number of bins.
    xmin : int
        The value of the lower edge of the first bin.
    xmax : int
        The value of the upper edge of the last bin.
    weights : str, optional
        The event weights or selection of events. The default is no weight.
    norm : bool, optional
        The flag for normalizing the histogram by its integral. The default is True.
    """
    name = uuid.uuid4().hex
    self.Draw('{variable}>>{name}({nbins!s}, {xmin!s}, {xmax!s})'.format(**locals()), weights, 'goff')
    h = ROOT.gDirectory.Get(name)
    h.SetTitle('')
    if norm:
        h.Scale(1. / h.Integral())
    h.SetDirectory(0)
    return h

ROOT.TTree.histogram = histogram

def select(self, selection):
    """Create and set an eventlist for a TTree.
    
    If an eventlist already exists, the new eventlist is
    created from the subset of events in the current eventlist.
    
    This method is dynamically patched onto the ROOT.TTree class.
    
    Parameters
    ----------
    name : str
        The name of the histogram. Because the histograms are created in the
        same global directory, their names should be unique.
    selection : str
        The selection expression.
        
    Returns
    -------
    self : This enables method chaining.
    """
    name = uuid.uuid4().hex
    self.Draw('>>{0}'.format(name), selection, 'goff')
    eventlist = ROOT.gDirectory.Get(name)
    eventlist.SetDirectory(0)
    if self.GetEventList():
        eventlist.Intersect(self.GetEventList())
    self.SetEventList(eventlist)
    return self
    
ROOT.TTree.select = select

# Load the HeppyV25 tree.
f_heppy = ROOT.TFile.Open('root://cmseos.fnal.gov///store/user/sjwang/ZnnHbb_Ntuple_Validation/Znn_HeppyV25.root')
tree_heppy = f_heppy.Get('tree')
print 'The HeppyV25 ntuple contains {0!s} total unweighted events.'.format(tree_heppy.GetEntriesFast())

# Load the NanoAOD tree.
f_nano = ROOT.TFile.Open('root://cmseos.fnal.gov///store/user/sjwang/ZnnHbb_Ntuple_Validation/Znn_NanoPost4.root')
tree_nano = f_nano.Get('Events')
print 'The NanoAOD ntuple contains {0!s} total unweighted events.'.format(tree_nano.GetEntriesFast())

# Apply the baseline and analysis phase space selections to the HeppyV25 ntuple.
(tree_heppy.select('Vtype == 2 || Vtype == 3 || Vtype == 4')
           .select('met_pt > 170')
           .select('HLT_BIT_HLT_PFMET110_PFMHT110_IDTight_v'
                   '|| HLT_BIT_HLT_PFMET120_PFMHT120_IDTight_v'
                   '|| HLT_BIT_HLT_PFMET170_HBHE_BeamHaloCleaned_v'
                   '|| HLT_BIT_HLT_PFMET170_NoiseCleaned_v'
                   '|| HLT_BIT_HLT_PFMET170_HBHECleaned_v')
           .select('HCMVAV2_mass > 0 && HCMVAV2_mass < 500 && HCMVAV2_pt > 120')
           .select('abs(TVector2::Phi_mpi_pi(HCMVAV2_phi-met_phi)) > 2')
           .select('Jet_pt[hJCMVAV2idx[0]] > 60'
                   '&& Jet_btagCMVAV2[hJCMVAV2idx[0]] > -0.5884'
                   '&& Jet_id[hJCMVAV2idx[0]] > 0'
                   '&& Jet_puId[hJCMVAV2idx[0]] > 0')
           .select('Jet_pt[hJCMVAV2idx[1]] > 35'
                   '&& Jet_btagCMVAV2[hJCMVAV2idx[1]] > -0.5884'
                   '&& Jet_id[hJCMVAV2idx[1]] > 0'
                   '&& Jet_puId[hJCMVAV2idx[1]] > 0')
           .select('Sum$(abs(TVector2::Phi_mpi_pi(Jet_phi-met_phi))<0.5 && Jet_pt>30 && Jet_puId>0)==0')
           .select('Flag_goodVertices'
                   '&& Flag_GlobalTightHalo2016Filter'
                   '&& Flag_HBHENoiseFilter'
                   '&& Flag_HBHENoiseIsoFilter'
                   '&& Flag_EcalDeadCellTriggerPrimitiveFilter')
)

# Apply the baseline and analysis phase space selections to the NanoAOD ntuple.
(tree_nano.select('Vtype == 2 || Vtype == 3 || Vtype == 4')
          .select('MET_pt > 170')
          .select('HLT_PFMET110_PFMHT110_IDTight'
                  '|| HLT_PFMET120_PFMHT120_IDTight'
                  '|| HLT_PFMET170_HBHE_BeamHaloCleaned'
                  '|| HLT_PFMET170_NoiseCleaned'
                  '|| HLT_PFMET170_HBHECleaned')
          .select('H_mass > 0 && H_mass < 500 && H_pt > 120')
          .select('abs(TVector2::Phi_mpi_pi(H_phi-MET_phi)) > 2')
          .select('Jet_pt[hJidx[0]] > 60'
                  '&& Jet_btagCMVA[hJidx[0]] > -0.5884'
                  '&& Jet_jetId[hJidx[0]] > 0'
                  '&& Jet_puId[hJidx[0]] > 0')
          .select('Jet_pt[hJidx[1]] > 35'
                  '&& Jet_btagCMVA[hJidx[1]] > -0.5884'
                  '&& Jet_jetId[hJidx[1]] > 0'
                  '&& Jet_puId[hJidx[1]] > 0')
          .select('Sum$(abs(TVector2::Phi_mpi_pi(Jet_phi-MET_phi))<0.5 && Jet_pt>30 && Jet_puId>0)==0')
          .select('Flag_goodVertices'
                  '&& Flag_globalTightHalo2016Filter'
                  '&& Flag_HBHENoiseFilter'
                  '&& Flag_HBHENoiseIsoFilter'
                  '&& Flag_EcalDeadCellTriggerPrimitiveFilter')
);

Welcome to JupyROOT 6.10/09
The HeppyV25 ntuple contains 1538976 total unweighted events.
The NanoAOD ntuple contains 409911 total unweighted events.


## Plots
---

### Generator Level
---

In [3]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('GenVbosons_pt', 50, 0, 500, weights='sign(genWeight)*(GenVbosons_pdgId==23)')
    hist_nano = tree_nano.histogram('GenPart_pt', 50, 0, 500, weights='sign(genWeight)*(GenPart_status==62 && GenPart_pdgId==23)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('p_{T}^{gen}(V) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [4]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('lheV_pt', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('LHE_Vpt', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('LHE p_{T}(V) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [5]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('lheHT', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('LHE_HT', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('LHE HT [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

### MET
---

In [6]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('met_pt', 40, 100, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('MET_pt', 40, 100, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('MET [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [7]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('met_phi', 32, -3.2, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('MET_phi', 32, -3.2, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#phi(MET)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

### Higgs
---

In [8]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('HCMVAV2_mass', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('H_mass', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('m(jj) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [9]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('HCMVAV2_pt', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('H_pt', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('p_{T}(jj) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [10]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('HCMVAV2_phi', 32, -3.2, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('H_phi', 32, -3.2, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#phi(jj)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [11]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('HCMVAV2_eta', 50, -5, 5, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('H_eta', 50, -5, 5, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#eta(jj)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

### Higgs Jet 1
---

In [12]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('hJCMVAV2idx[0]', 10, 0, 10, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('hJidx[0]', 10, 0, 10, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('Higgs Jet 1 Index')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [13]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_pt[hJCMVAV2idx[0]]', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_pt[hJidx[0]]', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('p_{T}(j_{1}) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [14]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_phi[hJCMVAV2idx[0]]', 32, -3.2, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_phi[hJidx[0]]', 32, -3.2, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#phi(j_{1})')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [15]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_eta[hJCMVAV2idx[0]]', 50, -5, 5, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_eta[hJidx[0]]', 50, -5, 5, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#eta(j_{1})')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [16]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_btagCMVAV2[hJCMVAV2idx[0]]', 100, -1, 1, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_btagCMVA[hJidx[0]]', 100, -1, 1, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('CMVA_{max}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

### Higgs Jet 2
---

In [17]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('hJCMVAV2idx[1]', 10, 0, 10, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('hJidx[1]', 10, 0, 10, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('Higgs Jet 2 Index')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [18]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_pt[hJCMVAV2idx[1]]', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_pt[hJidx[1]]', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('p_{T}(j_{2}) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [19]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_phi[hJCMVAV2idx[1]]', 32, -3.2, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_phi[hJidx[1]]', 32, -3.2, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.3
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#phi(j_{2})')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [20]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_eta[hJCMVAV2idx[1]]', 50, -5, 5, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_eta[hJidx[1]]', 50, -5, 5, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#eta(j_{2})')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [21]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Jet_btagCMVAV2[hJCMVAV2idx[1]]', 100, -1, 1, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Jet_btagCMVA[hJidx[1]]', 100, -1, 1, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('CMVA_{min}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

### Other Distributions
---

In [22]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('abs(TVector2::Phi_mpi_pi(HCMVAV2_phi-met_phi))', 32, 0, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('abs(TVector2::Phi_mpi_pi(H_phi-MET_phi))', 32, 0, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.3
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#||{#Delta#phi(V, jj)}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [23]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('(Jet_eta[hJCMVAV2idx[0]]-Jet_eta[hJCMVAV2idx[1]])', 50, -5, 5, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('(Jet_eta[hJidx[0]]-Jet_eta[hJidx[1]])', 50, -5, 5, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#Delta#eta(jj)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [24]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('abs(TVector2::Phi_mpi_pi(Jet_phi[hJCMVAV2idx[0]]-Jet_phi[hJCMVAV2idx[1]]))', 32, 0, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('abs(TVector2::Phi_mpi_pi(Jet_phi[hJidx[0]]-Jet_phi[hJidx[1]]))', 32, 0, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#Delta#phi(jj)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [25]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('((Jet_eta[hJCMVAV2idx[0]]-Jet_eta[hJCMVAV2idx[1]])**2 + (TVector2::Phi_mpi_pi(Jet_phi[hJCMVAV2idx[0]]-Jet_phi[hJCMVAV2idx[1]]))**2)**0.5', 50, 0, 5, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('((Jet_eta[hJidx[0]]-Jet_eta[hJidx[1]])**2 + (TVector2::Phi_mpi_pi(Jet_phi[hJidx[0]]-Jet_phi[hJidx[1]]))**2)**0.5', 50, 0, 5, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('#DeltaR(jj)')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [26]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Sum$(Jet_pt>30 && abs(Jet_eta)<2.4 && Jet_id>0 && Jet_puId>0)', 10, 0, 10, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Sum$(Jet_pt>30 && abs(Jet_eta)<2.4 && Jet_jetId>0 && Jet_puId>0)', 10, 0, 10, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('N_{j}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [27]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('Sum$(Jet_pt>30 && abs(Jet_eta)<2.4 && Jet_id>0 && Jet_puId>0 && Iteration$!=hJCMVAV2idx[0] && Iteration$!=hJCMVAV2idx[1])', 8, 0, 8, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('Sum$(Jet_pt>30 && abs(Jet_eta)<2.4 && Jet_jetId>0 && Jet_puId>0 && Iteration$!=hJidx[0] && Iteration$!=hJidx[1])', 8, 0, 8, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('N_{aj}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [28]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('MinIf$(abs(TVector2::Phi_mpi_pi(Jet_phi-met_phi)), Jet_pt>30 && Jet_id>0 && Jet_puId>0)', 32, 0, 3.2, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('MinIf$(abs(TVector2::Phi_mpi_pi(Jet_phi-MET_phi)), Jet_pt>30 && Jet_jetId>0 && Jet_puId>0)', 32, 0, 3.2, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.3
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('min #||{#Delta#phi(MET, j)}')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [29]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('nPVs', 50, 0, 50, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('PV_npvs', 50, 0, 50, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('# Primary Vertices')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()

In [30]:
with cms_figure.TDRStyle() as style:
    # It appears some style options need to be adjusted to look nicer for jsroot.
    style.SetLabelSize(0.035, 'XYZ')
    style.SetTitleSize(0.035, 'XYZ')
    style.SetTitleOffset(1.5, 'X')
    style.SetTitleOffset(1.8, 'Y')
    canvas = ROOT.TCanvas()
    canvas.SetRightMargin(0.08)
    # Create, style, and plot the histograms.
    hist_heppy = tree_heppy.histogram('MaxIf$(Jet_pt, Iteration$!=hJCMVAV2idx[0] && Iteration$!=hJCMVAV2idx[1])', 50, 0, 500, weights='sign(genWeight)')
    hist_nano = tree_nano.histogram('MaxIf$(Jet_pt, Iteration$!=hJidx[0] && Iteration$!=hJidx[1])', 50, 0, 500, weights='sign(genWeight)')
    y_max = max(hist_heppy.GetMaximum(), hist_nano.GetMaximum()) * 1.2
    hist_heppy.SetMaximum(y_max)
    hist_heppy.SetMinimum(0)
    hist_heppy.SetFillColorAlpha(ROOT.kBlue, 0.35)
    hist_heppy.SetXTitle('max p_{T}(aj) [GeV]')
    hist_heppy.SetYTitle('A.U.')
    hist_heppy.Draw('hist')
    hist_nano.SetFillColorAlpha(ROOT.kRed, 0.35)
    hist_nano.Draw('histsame')
    # Create and plot legend and labels.
    legend = ROOT.TLegend(0.65, 0.8, 0.9, 0.9)
    legend.SetBorderSize(0)
    legend.SetShadowColor(0)
    legend.SetTextSize(0.03)
    legend.AddEntry(hist_heppy, 'HeppyV25', 'f')
    legend.AddEntry(hist_nano, 'NanoAOD', 'f')
    legend.Draw()
    cms_figure.draw_labels('', extra_text='Simulation')
    canvas.Draw()